# **CIS 5300 Fall 2022 - Homework 3 - Sentiment Analysis with Deep Neural Networks**

In this assignmet you will use Pytorch, a popular deep learning library, to create sentiment classifiers using some of the models we have talked about in class. The goal of the assignment is to familiarize yourself with Pytorch, and a few of the issues specific to text processing using neural networks on GPUs. We will use Sentiment Analysis as an example classification problem, and consider a simple binary version of the problem. You will need to implement classifiers using Deep Averaging Networks, and different Recurrent Neural Networks (i.e. LSTMs). Finally, you will need to make a thorough comparison of these approaches, and do a qualitative analysis of the errors.

We have used a version of this as an assignment in 519 last semester to introduce NLP with deep networks. You will be asked to go much further here, but if you are familiar with parts of this assignment, you may reuse.

## 1. Introduction to Pytorch

PyTorch is an optimized tensor library for deep learning using GPUs and CPUs. This homework will be using PyTorch to build Neural Networks to solve an NLP classification problem.

If you are new to using the framework it is worthwhile to spend an hour reviewing the concepts of tensors, autograd, training classifiers etc in [this tutorial](https://pytorch.org/tutorials/beginner/deep_learning_60min_blitz.html).

Refer to [this tutorial](https://pytorch.org/tutorials/beginner/introyt/modelsyt_tutorial.html) to learn more about how to build models with Pytorch.

## 2. Stanford Sentiment Treebank(SST) Data Loading

#### Stanford Sentiment Treebank(SST)

We'll introduce the [Stanford Sentiment Treebank](https://nlp.stanford.edu/sentiment/index.html) (SST) dataset. SST was introduced by [(Socher et al. 2013)](http://nlp.stanford.edu/~socherr/EMNLP2013_RNTN.pdf) consists of 11,855 sentences drawn from a corpus of movie reviews (originally from Rotten Tomatoes), each labeled with sentiment on a five-point scale. 

An example of the five-point scale is:
```
sentence: [A warm , funny , engaging film .]
label:    4 (very positive)
```

**Note:** Unlike most classification datasets, SST is also a _treebank_, which means each sentence is associated with a tree structure that decomposes it into subphrases. So for the example above, we'd also have sentiment labels for `[warm , funny]` and `[engaging film .]` and so on. The tree structure will comes in handy for complex NLP tasks and we will be using it briefly to analyze an example that has negation. The data is distributed as serialized trees in [S-expression](https://en.wikipedia.org/wiki/S-expression) form, like this:
```
(4 (4 (2 A) (4 (3 (3 warm) (2 ,)) (3 funny))) (3 (2 ,) (3 (4 (4 engaging) (2 film)) (2 .))))
```
Generally, we can exploit these richer annotations when training a classifier by also using phrases as training instances. This augmented training signal is important for getting good performance for models that have many parameters.

We've downloaded the dataset and parse the S-expressions into a dataframe. 



### 2.1 Importing packages

In [ ]:
#@title
from __future__ import division
import os, sys, re, json, time, datetime, shutil
import itertools, collections
from importlib import reload

import random 
import numpy as np
import pandas as pd
import os
import sys
import matplotlib.pyplot as plt
from numpy.linalg import *
np.random.seed(42)  # don't change this line

import base64

# NLTK, NumPy, and Pandas.
import nltk
from nltk.tree import Tree
from numpy import random as rd
import random

import collections
import re
import time
import itertools
from collections import defaultdict, Counter

import glob
from argparse import ArgumentParser

#Pytorch
import torch
import torch.nn as nn
import torch.nn.functional as F

import torch.optim as optim
from torch.utils.data import Dataset, DataLoader


!pip3 install wget

### 2.2 Downloading Required files
[train parquet file](https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/train.parquet)

[dev parquet file](https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/dev.parquet)

[test parquet file](https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/test.parquet)

[tokens in training data](https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/train_tokens.txt)

In [ ]:
#@title 
!wget  -c  https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/train_tokens.txt
!wget  -c  https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/train.parquet
!wget  -c  https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/dev.parquet
!wget  -c  https://www.cis.upenn.edu/~myatskar/teaching/cis519/a5/test.parquet

If the cells above fails to download all the files, rerun a couple of times or download them and add them manually.

In [ ]:
train_file = "train.parquet" 
dev_file = "dev.parquet" 
test_file = "test.parquet" 
vocab_file = "train_tokens.txt" 

### 2.3 Parsing Tree Structure 
 Helper code to process the data

In [ ]:
# Constants for use by other modules.
START_TOKEN = u"<s>"
END_TOKEN   = u"</s>"
UNK_TOKEN   = u"<unk>"

In [ ]:
#@title
class SSTDataset(object):
    Example_fields = ["tokens", "ids", "label", "is_root", "root_id"]
    Example = collections.namedtuple("Example", Example_fields)

    def canonicalize(self, raw_tokens):
        wordset=(self.vocab.wordset if self.vocab else None)
        return canonicalize_words(raw_tokens, wordset=wordset)

    def __init__(self,train_file,dev_file,test_file,vocab_file,V=20000):
        self.vocab = None
        self.train = pd.read_parquet(train_file)
        self.dev = pd.read_parquet(dev_file)
        self.test = pd.read_parquet(test_file)
        train_words =[]
        with open(vocab_file) as f:
            train_words = f.readlines()
        train_words = [w.strip() for w in train_words]
        # Build vocabulary over training set
        self.vocab = Vocabulary(train_words, size=V)
        # print("Train set has {:,} words".format(self.vocab.size))
        self.target_names = [0,1]

    def get_filtered_split(self, split='train',is_root = True):
        df = getattr(self, split)
        if is_root:
            df = df[df.is_root]
        return df

    def as_padded_array(self, split='train', max_len=40, pad_id=0,is_root = True):
        df = self.get_filtered_split(split,is_root)
        x, ns = pad_np_array(df.ids, max_len=max_len, pad_id=pad_id)
        y = np.empty((1,1))
        if split != 'test':
            y  = np.array(df.label, dtype=np.int32)
        return x, ns, y

    def as_sparse_bow(self, split='train',is_root = True):
        from scipy import sparse
        df = self.get_filtered_split(split,is_root)
        x = id_lists_to_sparse_bow(df['ids'], self.vocab.size)
        if split != 'test':
            return x, np.array(df.label, dtype=np.int32)
        return x

def require_package(package_name):
    import pkgutil
    import subprocess
    import sys
    if not pkgutil.find_loader(package_name):
        subprocess.check_call([sys.executable, '-m', 'pip', 'install', package_name])

def canonicalize_digits(word):
    if any([c.isalpha() for c in word]): return word
    word = re.sub("\d", "DG", word)
    if word.startswith("DG"):
        word = word.replace(",", "") # remove thousands separator
    return word

def canonicalize_word(word, wordset=None, digits=True):
    word = word.lower()
    if digits:
        if (wordset != None) and (word in wordset): return word
        word = canonicalize_digits(word) # try to canonicalize numbers
    if (wordset == None) or (word in wordset):
        return word
    else:
        return UNK_TOKEN

def canonicalize_words(words, **kw):
    return [canonicalize_word(word, **kw) for word in words]


def pad_np_array(example_ids, max_len=250, pad_id=0):
    arr = np.full([len(example_ids), max_len], pad_id, dtype=np.int32)
    ns = np.zeros([len(example_ids)], dtype=np.int32)
    for i, ids in enumerate(example_ids):
        cpy_len = min(len(ids), max_len)
        arr[i,:cpy_len] = ids[:cpy_len]
        ns[i] = cpy_len
    return arr, ns

def id_lists_to_sparse_bow(id_lists, vocab_size):
    from scipy import sparse
    ii = []  # row indices (example ids)
    jj = []  # column indices (token ids)
    for row_id, ids in enumerate(id_lists):
        ii.extend([row_id]*len(ids))
        jj.extend(ids)
    x = sparse.csr_matrix((np.ones_like(ii), (ii, jj)),
                          shape=[len(id_lists), vocab_size])
    return x

class Vocabulary(object):

    START_TOKEN = START_TOKEN
    END_TOKEN   = END_TOKEN
    UNK_TOKEN   = UNK_TOKEN

    def __init__(self, tokens, size=None,
                 progressbar=lambda l:l):
        self.unigram_counts = Counter()
        self.bigram_counts = defaultdict(lambda: Counter())
        prev_word = None
        for word in progressbar(tokens):  # Make a single pass through tokens
            self.unigram_counts[word] += 1
            self.bigram_counts[prev_word][word] += 1
            prev_word = word
        self.bigram_counts.default_factory = None  # make into a normal dict

        # Leave space for "<s>", "</s>", and "<unk>"
        top_counts = self.unigram_counts.most_common(None if size is None else (size - 3))
        vocab = ([self.START_TOKEN, self.END_TOKEN, self.UNK_TOKEN] +
                 [w for w,c in top_counts])

        # Assign an id to each word, by frequency
        self.id_to_word = dict(enumerate(vocab))
        self.word_to_id = {v:k for k,v in self.id_to_word.items()}
        self.size = len(self.id_to_word)
        if size is not None:
            assert(self.size <= size)

        # For convenience
        self.wordset = set(self.word_to_id.keys())

        # Store special IDs
        self.START_ID = self.word_to_id[self.START_TOKEN]
        self.END_ID = self.word_to_id[self.END_TOKEN]
        self.UNK_ID = self.word_to_id[self.UNK_TOKEN]

    def words_to_ids(self, words):
        return [self.word_to_id.get(w, self.UNK_ID) for w in words]

    def ids_to_words(self, ids):
        return [self.id_to_word[i] for i in ids]

    def ordered_words(self):
        """Return a list of words, ordered by id."""
        return self.ids_to_words(range(self.size))


### 2.4 Brief Look at SSTDataset Functionality



In [ ]:
ds = SSTDataset(train_file, dev_file, test_file,vocab_file, V=20000)

A few members of the `SSTDataset()` class that we will be using are:
- **`ds.vocab`**: a `vocabulary.Vocabulary` object managing the model vocabulary.
- **`ds.{train,dev,test}`**: a Pandas DataFrame containing the _processed_ examples, including all subphrases. `label` is the target label, `is_root` denotes whether this example is a root node (full sentence), and `tokens` are the tokenized words from the original sentence.

Note if you set `root_only=True` the dataframe will return only examples corresponding to whole sentences. If you set `root_only=False` the dataframe will return examples for all phrases.

In [ ]:
is_root = False

## 3. [Deep Averaging Networks](https://people.cs.umass.edu/~miyyer/pubs/2015_acl_dan.pdf)

We are going to implement the deep averaging networks

![dan](https://miro.medium.com/max/904/1*0LezMYWUk3pXptoMdO5M_Q.png)


Vector space models for natural language processing (NLP) represent words using low dimensional vectors called embeddings. To apply vector space
models to sentences or documents, one must first select an appropriate composition function, which combines multiple words into a single vector.

Composition functions fall into two classes: unordered and syntactic. Unordered functions treat input texts as bags of word embeddings, while syntactic functions take word order and sentence structure
into account. Syntactic functions outperform unordered functions on many tasks. However, there is a tradeoff: syntactic functions require more training time and computing resources. 

The deep averaging network (DAN) is a deep unordered model which that obtains near state-of-the-art accuracies on a variety of sentence and document-level tasks with just minutes of training time on an average laptop computer. It
works in three simple steps:
1. Take the vector average of the embeddings
associated with an input sequence of tokens
2. Pass that average through one or more feedforward layers
3. Perform (linear) classification on the final
layer’s representation

Furthermore, DANs, can be effectively trained on data that have high syntactic variance. The model works by magnifying tiny but meaningful differences in the vector average.

We are going to use DANs for the same classification problem.

### 3.1 [Glove Embeddings](https://nlp.stanford.edu/projects/glove/) 
We are downloading pretrained glove word vectors that has been trained on Common Crawl data, a snapshot of the whole web.
These embeddings serve as excelent initilizations for embeddings our model needs.
Downloading glove embeddings (This will take around 10 minutes) 

In [ ]:
#this takes about 10 minutes to run
!wget -nc https://downloads.cs.stanford.edu/nlp/data/glove.840B.300d.zip
!unzip glove.840B.300d.zip
!ls -lat

In [ ]:
glove_file = "glove.840B.300d.txt"

In [ ]:
train_x, train_ns, train_y = ds.as_padded_array("train",is_root = is_root)
dev_x, dev_ns, dev_y = ds.as_padded_array("dev",is_root = is_root)
test_x, test_ns,_  = ds.as_padded_array("test",is_root = is_root)

print("Training set:   x = {:s} sparse, ns={:s}, y = {:s}".format(str(train_x.shape), str(train_ns.shape),
                                                str(train_y.shape)))
print("Validation set: x = {:s} sparse, ns={:s}, y = {:s}".format(str(dev_x.shape), str(dev_ns.shape),
                                                str(dev_y.shape)))
print("Test set:       x = {:s} sparse, ns={:s}".format(str(test_x.shape), str(test_ns.shape)))

In [ ]:
#look at the format of the file
!head glove.840B.300d.txt

#### Get Glove embeddings
In this section we want to populate the `glove` dictionary with a mapping of word to the embedding. Remember: the embedding should be an `np.array` of type `np.float` The glove dictionary should only have words that are present in the train vocabulary. 


Hint: For getting the word and corresponding embedding from the glove file, remember refer to the above structure of the word to embedding mapping.

In [ ]:
#takes about 1 minute to read through the whole file and find the words we need. 
def get_glove_mapping(vocab, file):
    """
    Gets the mapping of words from the vocabulary to pretrained embeddings
    
    INPUT:
    vocab       - set of vocabulary words
    file        - file with pretrained embeddings

    OUTPUT:
    glove_map   - mapping of words in the vocabulary to the pretrained embedding
    
    """
    
    glove_map = {}
    with open(file,'rb') as fi:
        for l in fi:
            try:
                #### STUDENT CODE HERE ####
                
                #### STUDENT CODE ENDS HERE ####
            except:
                #some lines have urls, we don't need them.
                pass
    return glove_map

In [ ]:
vocab_set = set(ds.vocab.ordered_words())
glove_map = get_glove_mapping(vocab_set,glove_file)

### 3.2 Embedding Matrix

Fill in the dimensions required for Embedding matrix

In [ ]:
def get_dimensions():
    d_out =  #number of outputs
    n_embed =  #size of the dictionary of embeddings
    d_embed =  # the size of each embedding vector
    return d_out, n_embed, d_embed
d_out,n_embed,d_embed = get_dimensions()

#### Initializing the Embedding matrix

Create a embedding_matrix for the parameters to be learnt. Initialize the embedding matrix for a particular id with the glove embedding for the same id. If you do not find a particular word, initialize the weight matrix with `np.random.normal`

Hint: `ds.vocab.ordered_words()` can give you the mapping of id to words. `glove` has the embeddings you need.

In [ ]:
def get_embedding_matrix(n_embed, d_embed, glove_map):
    """
    Initialize the weight matrix
    
    INPUT:
    n_embed         - size of the dictionary of embeddings
    d_embed         - the size of each embedding vector

    OUTPUT:
    embedding_matrix  - matrix of mapping from word id to embedding 
    """
    #### STUDENT CODE HERE #### 
    #### STUDENT CODE ENDS HERE ####
    return embedding_matrix

In [ ]:
embedding_matrix = get_embedding_matrix(n_embed, d_embed, glove_map)
embedding_data = (embedding_matrix.shape, embedding_matrix[:155])

### 3.3 Embedding Layer
Use the embedding matrix to create the embedding layer by using `nn.Embedding`.

In [ ]:
def create_emb_layer(embedding_matrix, non_trainable=False):
    """
    Create the embedding layer
    
    INPUT:
    embedding_matrix  - matrix of mapping from word id to embedding
    non_trainable   - Flag for whether the weight matrix should be trained. 
                      If it is set to True, don't update the gradients

    OUTPUT:
    emb_layer       - embedding layer 
    
    """
    #### STUDENT CODE HERE ####
    #### STUDENT CODE ENDS HERE ####

    return emb_layer

### 3.4 Defining the Dataloader 

For the ease of batch processing, we are defining the following to use the functionality of the Dataloader in Pytorch. 

You can read more about it in [this tutorial](https://pytorch.org/tutorials/beginner/basics/data_tutorial.html).

Note: The process of creating a mask for dealing with word dropout and variable length sequences.

In [ ]:
class SSTpytorchDataset(Dataset):
    def __init__(self, sst_ds, word_dropout = 0.3, split='train'):
        super(SSTpytorchDataset, self).__init__()
        assert split in ['train', 'test', 'dev'], "Error!"
        self.ds = sst_ds
        self.split = split
        self.word_dropout = word_dropout
        self.data_x, self.data_ns, self.data_y = self.ds.as_padded_array(split,is_root =is_root)
        self.mask = np.zeros_like(self.data_x)

    def __len__(self):
        return self.data_x.shape[0]
    
    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()
        y = 2
        if self.split != 'test':
            y = self.data_y[idx]
            
        mask = np.zeros(len(self.data_x[idx]))
        sentl = self.data_ns[idx]
        total_dropped = 0
        for j in range(0,sentl):
            mask[j] = 1
            if self.split == 'train': 
                rv = random.random()
                if rv  < self.word_dropout: 
                    mask[j] = 0 
                    total_dropped+=1
        if total_dropped >= sentl: 
            mask[0] = 1
        for i in range(sentl,len(self.data_x[idx])):
            mask[i] = 0
        self.mask[idx] = mask        
        return self.data_x[idx], self.data_ns[idx], self.mask[idx], sentl, y
        

### 3.5 Defining DAN Architecture

#### Masking in Deep Averaging Networks

A lot of NLP applications use masking and deal with variable sequence length and word maksing. 
You have to perform the following steps:


1. Change the view of the mask so it extends to the embeddings size
2. Calculate the number of words after dropout `den`
3. Eliminate the tokens that aren't in the mask, and sum the rest `num`
4. return `x = num/den` 

Note: You can look at [expand](https://pytorch.org/docs/stable/generated/torch.Tensor.expand.html) in pytorch. 

Implement this logic in the masked mean function. 

You will also need define the feedforward layers required for the final output of the classifier. We suggest you start simple, and first implement a linear classifier over the average of words embeddings. Then, introduce a feedforward neural network that operates over the average embeddings. Remeber, you must include non-linearities in your feed foward network. Experiment with different depths.

#### Defining the architecture for Deep Averaging Networks

In [ ]:
import random as random

class DAN(nn.Module):

    def __init__(self,
                 n_embed=20000,
                 d_embed=300,
                 d_hidden=100,
                 d_out=2,
                 layer_dropout = 0.2,
                 embeddings=None,
                 depth = 2):
        super(DAN, self).__init__()

        self.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.embed = create_emb_layer(embedding_matrix,False) 
        #### STUDENT CODE HERE ####
        ### We need to create the layers to construct the output of the classifier. 
        ### One possible implementation uses the "nn.Seqential" module, which chains together multiple layers.
        #### STUDENT CODE ENDS HERE ####

    def masked_mean(self,v, mask):
        """
        Create the masked mean
        
        INPUT:
        v       - input
        mask    - mask that has 0 and 1 for all th tokens in the input
                  0 corresponds to dropping the token and 1 corresponds to keeping the token

        OUTPUT:
        x       - average  
        
        """
        (batch, max_sent, d_embed ) = v.size()      
        mask.requires_grad = False

        #### STUDENT CODE HERE ####
        mask = #change the view of the mask so it extends to the embeddings size
        den =  #the number surviving words
        num =  #eliminate the tokens that aren't in the mask, and sum
        x =    #average
        #### STUDENT CODE ENDS HERE ####
        return x

    def forward(self, text, mask):
        x = text
        x = self.embed(x)
        x = self.masked_mean(x,mask)
        x = self.feedforward_layers(x)
        return x

### 3.6 Training the Deep Averaging Network

In [ ]:
def train(model, lr = .005, drop_out = 0, word_dropout = .3, batch_size = 16, weight_decay = 1e-5, model_type= "DAN"):
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    trainset = SSTpytorchDataset(ds, word_dropout, 'train')
    testset = SSTpytorchDataset(ds, word_dropout, 'test')
    devset = SSTpytorchDataset(ds, word_dropout, 'dev')

    train_iter = DataLoader(trainset, batch_size, shuffle=True, num_workers=0)
    test_iter = DataLoader(testset, batch_size, shuffle=False, num_workers=0)
    dev_iter = DataLoader(devset, batch_size, shuffle=False, num_workers=0)
    
    model = model
    model.to(device)

    optimizer = optim.AdamW(model.parameters(), lr=lr, weight_decay = weight_decay)


    acc, val_loss = evaluate(dev_iter, model, device, model_type)
    best_acc = acc

    print(
        'epoch |   %        |  loss  |  avg   |val loss|   acc   |  best  | time | save |')
    print(
        'val   |            |        |        | {:.4f} | {:.4f} | {:.4f} |      |      |'.format(
            val_loss, acc, best_acc))

    iterations = 0
    last_val_iter = 0
    train_loss = 0
    start = time.time()
    _save_ckp = ''
    for epoch in range(epochs):
        # train_iter.init_epoch()
        n_correct, n_total, train_loss = 0, 0, 0
        last_val_iter = 0
        for batch_idx, batch in enumerate(train_iter):
            # switch model to training mode, clear gradient accumulators
            model.train()
            optimizer.zero_grad()
            iterations += 1

            data, ns, mask, lens, label = batch
            data = data.to(device)
            label = label.to(device).long()
            mask = mask.to(device).long()
            if model_type == "LSTM":
                answer = model(data, mask, lens)
            else:
                answer = model(data, mask)

            loss = criterion(answer, label)

            loss.backward()
            optimizer.step()

            train_loss += loss.item()
            print('\r {:4d} | {:4d}/{} | {:.4f} | {:.4f} |'.format(
                epoch, batch_size * (batch_idx + 1), len(trainset), loss.item(),
                       train_loss / (iterations - last_val_iter)), end='')

            if iterations > 0 and iterations % dev_every == 0:
                acc, val_loss= evaluate(dev_iter, model, device, model_type)
                if acc > best_acc:
                    best_acc = acc
                    torch.save(model.state_dict(), save_path)
                    _save_ckp = '*'

                print(
                    ' {:.4f} | {:.4f} | {:.4f} | {:.2f} | {:4s} |'.format(
                        val_loss, acc, best_acc, (time.time() - start) / 60,
                        _save_ckp))

                train_loss = 0
                last_val_iter = iterations
    model.load_state_dict(torch.load(save_path)) #this will be the best model
    test_y_pred = evaluate(test_iter, model, device, model_type, "test")
    print("\nValidation Accuracy : ", evaluate(dev_iter,model, device, model_type))
    return best_acc, test_y_pred


In [ ]:

def evaluate(loader, model, device, model_type = "DAN", split = "dev"):
    model.eval()
    n_correct, n = 0, 0
    losses = []
    y_pred = []
    with torch.no_grad():
        for batch_idx, batch in enumerate(loader):
            data, ns, mask, lens, label = batch
            data = data.to(device)
            label = label.to(device).long()
            mask = mask.to(device).long()
            if model_type == "LSTM":
                answer = model(data, mask, lens)
            else:
                answer = model(data, mask)
            if split != "test":
                n_correct += (torch.max(answer, 1)[1].view(label.size()) == label).sum().item()
                n += answer.shape[0]
                loss = criterion(answer, label)
                losses.append(loss.data.cpu().numpy())
            else:
                y_pred.extend(torch.max(answer, 1)[1].view(label.size()).tolist())
    if split != "test":
        acc = 100. * n_correct / n
        loss = np.mean(losses)
        return acc, loss
    else:
        return y_pred


The following code will train the averaging network on the training data after which it will return the accuracy achieved on the validation set as well as the predictions for the test set. 

In [ ]:
criterion = nn.CrossEntropyLoss()
lr = 0.01
drop_out = 0
word_dropout = 0.1
weight_decay = 1e-5
torch.manual_seed(1234)
batch_size = 128
dev_every = 100
epochs = 3 
save_path = "best_model"
model = DAN(n_embed=n_embed, d_embed=d_embed, d_hidden=300, d_out=d_out, layer_dropout=drop_out)
dev_value, test_y_pred = train(model,lr, drop_out, word_dropout, batch_size, weight_decay, "DAN") 

### 4.3 Self Exploration

This is where you experiment with different configurations of training (learning rate and batch size), and the network (dropout rates, depth, hidden sizes) and report which worked best. Illustrate your expermiments with in the form of a table (learning rate vs dev accuracy and batch size vs dev accuracy). When doing this validation, it is not required to train to convergence.


Write the predictions for the test dataset into the file "test_labels_DAN.txt" to be uploaded along with your submissions. We will evaluate your best configuration to see if it is within the range we expect for performance.

## 4. LSTM Networks



![LSTM](https://miro.medium.com/max/1400/1*-kBdBYzR7lpimgb3AIRkOw.png)

LSTM stands for Long Short-Term Memory Network and it is a type of Recurrent Neural Network (RNN). As you recall from the lecture, Simple RNNs can struggle with exploding or vanishing gradients and LSTMs try to improve this issue. For the next part of the coding exercise, you will implement an LSTM to solve the classification problem.

There are multiple ways to get the classification output from the hidden states of an RNN. For example, you may take the last hidden output, or you may aggregate the hidden states, use max or mean operations. Include a discussion of which method you have used in your report. 

**Hint:** You might want to think about how to handle different length sentences. You can use [pack_padded_sequence](https://pytorch.org/docs/stable/generated/torch.nn.utils.rnn.pack_padded_sequence.html) and [pad_packed_sequence](https://pytorch.org/docs/stable/generated/torch.nn.utils.rnn.pad_packed_sequence.html) to achieve this.

**Note:** Bi-directional LSTMs require a concatnation of the output. Consider the PyTorch documentation carefully https://pytorch.org/docs/stable/generated/torch.nn.LSTM.html?highlight=lstm#torch.nn.LSTM 

### 4.1 Defining the architecture for LSTM Networks

This is where you define the architecture for the LSTM Network. Ensure that you also handle the cases where you have to define a Bi-directional LSTM network.

In [ ]:
import random as random
from torch.nn.utils.rnn import pack_padded_sequence, pad_packed_sequence
from torch.nn import LSTM, GRU

class LSTM_Classifier(nn.Module):

    def __init__(self,
                 n_embed=20000,
                 d_embed=300,
                 d_hidden=150,
                 d_out=2,
                 embeddings=None,
                 nl = 2,
                 bidirectional = True
                 ):
        super(LSTM_Classifier, self).__init__()

        self.d_hidden = d_hidden
        self.bidrectional = bidirectional
        self.num_layers = nl

        self.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.embed = create_emb_layer(embedding_matrix,False)
        #### STUDENT CODE STARTS HERE ####
        self.lstm = #Initialize the LSTM
        self.fc_out = #Get the output for the LSTM from the hidden layers (Consider the bidirectional LSTM case too)
        #### STUDENT CODE ENDS HERE ####

    def forward(self, text, mask, seq_lengths):

        batch_size = text.size()[0]

        #### STUDENT CODE STARTS HERE ####
        #Fill the missing pieces for the forward pass
        #### STUDENT CODE ENDS HERE ####
        return x

### 4.2 Training Loop

In [ ]:
torch.manual_seed(1234)
criterion = nn.CrossEntropyLoss()
batch_size = 64
epochs = 3
dev_every = 100
lr = 0.01
save_path = "best_model"
drop_out = 0
word_dropout = 0
weight_decay = 0

model = LSTM_Classifier(n_embed=n_embed, d_embed=d_embed, d_hidden=150, d_out=d_out)
dev_value, test_y_pred = train(model, lr, drop_out, word_dropout, batch_size, weight_decay, "LSTM") 

### 4.3 Self Exploration

Experiment with different types of RNN networks and see which one works the best for the task (Bidirectional LSTM, GRU, Simple RNN). You have to report the difference in performance between these in your report. You should also tune the hypeparamters (learning rate and batch size, hidden dimension size) and report which worked best. Illustrate your expermiments with in the form of a table (learning rate vs dev accuracy and batch size vs dev accuracy).


## 5.0 Qualitative Analysis

At this point, you should have built at least two types of models: an order agnostic model and at least two RNN based model. 

1.   Sample some errors between these models, from example instances that contain negation (i.e. not) words. Do the models behave qualitatively differnely?
2.   Analyze the performance of the model as a function of the length of the input. Plot length of a sample versus performance, by bucketing length. Do your models perform have any qualitative differences?



## Submission:





These are the files you have to submit to gradescope

1.   Report
2.   Download your jupyter notebook as a python file and submit it as "homework3.py". Comment out all lines that start with "!".
3.   The test predictions on DAN in a txt file (no headers) as "test_labels_DAN.txt"
4. The test predictions on your best Recurrent Neural Network model in a txt file (no headers) as "test_labels_RNN.txt"



Your report must include the following:

Deep Averaging Networks [25 Points]:
1. A description of hyper parameters that worked best for your model.
2. Validation accuracy for the best hyper parameter.
3. Table of learning rate vs validation accuracy for all learning rates tried.
4. Table of batch size vs validation accuracy for all batch sizes tried.

RNN Networks [25 Points]:

1. A description of which models you tried and what worked best.
2. Validation accuracy for the best hyper parameter on your best model.
3. Table of learning rate vs validation accuracy for all learning rates tried.
4. Table of batch size vs validation accuracy for all batch sizes tried.

Comparison [15 Points]: 
A comparison between Deep Averaging Networks and RNNs (you can consider factors like time to train, accuracy etc), including elements suggested in Qualitative Analysis above.

## Extra Credit (EC):
Manually construct failure cases (inputs) for classifier (eg: negation and metaphor). Consider both false positive and false negative cases. Extra credit will be awarded if you can describe a pattern for the new failure cases you have discovered, and report at least 5 instances not from the dataset that demonstrate the pattern (up to 10 points)




